In [53]:
import os
import json
from pathlib import Path
from dotenv import load_dotenv
from llama_cpp import Llama
from transformers import AutoTokenizer, PreTrainedTokenizer
from pymongo import MongoClient
from datetime import datetime, timedelta
from django.shortcuts import render
from django.http import JsonResponse, FileResponse
from langchain_openai import ChatOpenAI
from pymongo import MongoClient
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import FAISS
from langchain.text_splitter import CharacterTextSplitter
from langchain_core.documents import Document
import re
# retriever 사용을 위한 라이브러리
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

import certifi

# 파이썬 서드파티 라이브러리
import pandas as pd
from bs4 import BeautifulSoup, Comment

In [33]:
# 경로
current_dir = Path().resolve().parent
hankyung_path = rf'{current_dir}\datas\news_data\hankyung_data.json'
maekyung_path = rf'{current_dir}\datas\news_data\maekyung_data.json'
yna_path = rf'{current_dir}\datas\news_data\yna_data.json'

In [34]:
def preprocess_text(text):
    # 텍스트 전처리 / string으로 받아서 string으로 반환합니다.
    # URL 제거
    text = re.sub(r"http\S+", "", text)
    # 특수 문자 제거 (기본 구두점은 보존)
    text = re.sub(r"[^\w\s.,!?]", "", text)
    # 소문자 변환
    text = text.lower()
    # 공백 정리
    text = re.sub(r"\s+", " ", text).strip()
    return text

In [35]:
input_string = '반도체 시장에 대한 뉴스를 알려줘'
load_dotenv()
api_key = os.getenv('OPENAI_API_KEY')
llm = ChatOpenAI(
    model_name='gpt-4o',
    api_key=api_key
)
# mongoDB에서 데이터를 가져오기
# cluster = MongoClient(os.environ.get("mongo")) # 클러스터
# db = cluster[''] # 유저 정보
# collection = db[""] # 내가 지정한 컬렉션 이름
# 지금은 임의로 데이터를 넣어놨지만 실제로는 데이터를 가져와야한다.
maekyung_path = rf'{current_dir}\datas\news_data\maekyung_data.json'
with open(maekyung_path, 'r', encoding = 'utf-8') as f:
    data = json.load(f)

In [36]:
def news_preprocess(news_content: str) -> str:

    soup = BeautifulSoup(news_content, 'html.parser')
    
    # BeautifulSouo로 일부 tag 제거
    # 이미지 제거
    for tag in soup.find_all(lambda tag: tag.name == 'div' and tag.has_attr('style') and tag['style'] == 'width:100%; text-align: center;'):
        tag.decompose()

    # 스크립트 제거
    for tag in soup.find_all(lambda tag: tag.name == 'script'):
        tag.decompose()

    # 주석 제거
    for comment in soup.find_all(string=lambda text: isinstance(text, Comment)):
        comment.extract()

    # MK시그널 링크 제거
    for tag in soup.find_all('a', {"class": "ix-editor-text-link"}):
        tag.decompose()

    # ------------------------------------------------------------------------------------------------------------------------------------

    # replace 및 정규표현식으로 제거
    # 본문 태그 제거 및 양 끝에 있는 \n같은 화이트스페이스 제거
    content = [str(s) for s in soup.div.contents]
    content = ''.join(content).strip()

    # [김진우 기자], [김진우 기자 / 권용희 기자] 같은 불필요한 정보 제거
    content = re.sub(pattern=r'\[.+?/?.+?기자\]', repl='', string=content)

    # MK시그널의 쓰잘데기 없는 광고 문구 제거
    content = re.sub(pattern=r'※ 매일경제 AI기자.*?앱을 다운로드하세요\!', repl='', string=content)
    content = re.sub(pattern=r'이 종목의 향후 매매신호를 받으려면 MK시그널.*?실시간으로 확인할 수 있습니다\.', repl='', string=content)
    content = re.sub(pattern=r'MK시그널은 AI가 국내·미국 주식.*?정보 서비스입니다\.', repl='', string=content)
    content = re.sub(pattern=r'국내 주식과 더불어 미국 주식.*?신호 받아보세요\!', repl='', string=content)
    content = re.sub(pattern=r'인공지능\(AI\) 기반 매매신호 제공 앱.*?투자를 시작하세요\!', repl='', string=content)
    content = re.sub(pattern=r'MK시그널 현재.*?진행중\!', repl='', string=content)

    # '나현준의 데이터로 세상 읽기'에서 불필요한 정보 제거
    content = re.sub(pattern=r'◆\s*매경 포커스\s*◆', repl='', string=content)

    # amp; 제거
    content = content.replace('amp;', '')

    # 과도한 <br/>\n들을 줄이기
    content = re.sub(pattern=r'(\s+<br/>){3,}', repl=r"\n <br/>\n<br/>", string=content)

    # 양 끝자락에 있는 화이트스페이스 제거
    content = content.strip()

    # 오른쪽 끝자락에 있는 r'\s*?(<br/>\s*?)+?$'패턴들을 제거
    content = re.sub(pattern=r'\s*?(<br/>\s*?)+?$', repl='', string=content)

    # 왼쪽 끝자락에 있는 ^\s*?(<br/>\s*?)+?패턴들을 제거
    content = re.sub(pattern=r'^\s*?(<br/>\s*?)+?', repl='', string=content)

    # 양 끝자락에 있는 화이트스페이스 제거
    content = content.strip()
    return content

In [37]:
news_data = []

for news in data:
    news['news_content'] = news_preprocess(news['news_content'])
    news_data.append(news)

In [38]:
news_data[:5]

[{'news_title': '무역전쟁엔 스페셜티 기업이 성공··· “2월은 저가매수 기회”',
  'news_first_upload_time': '2025-02-04 18:11',
  'news_last_upload_time': None,
  'news_author': '정재원 기자',
  'news_content': '<div style="display:box;border-left:solid 4px rgb(228, 228, 228);padding-left: 20px; padding-right: 20px;">\n  4일 메리츠증권 보고서\n  <br/>\n  테슬라 자율주행 기술처럼\n  <br/>\n  전문성 갖춘 국내 기업 찾아라\n </div>\n <br/>\n<br/>\n 글로벌 통상환경의 ‘불확실성’ 파도로부터 살아남을 수 있는 국내 주식은 ‘스페셜티’(Specialty·전문성)를 갖춘 기업이라는 분석이 나왔다.\n <br/>\n<br/>\n 4일 이수정 메리츠증권 연구원은 2월 투자전망 보고서에서 “국내 주식은 위험 회피 현상이 지나면 장기적으로 무역전쟁의 반사수혜가 기대된다”며 이번 달을 스페셜티 기업들의 저가매수 기회로 삼으라고 조언했다.\n <br/>\n<br/>\n 이수정 연구원은 스페셜티 기업의 대표적 예시로 테슬라를 꼽았다. 테슬라는 독보적인 자율주행 기술을 무기로 시장을 이끌어 온 업계 선두주자다.\n <br/>\n<br/>\n 이 연구원은 “테슬라 자율주행의 사고 전 평균 주행거리는 594만마일(956만km)로, 미국 수동운전자들의 운전 평균값인 70만마일(112만km)와 크게 차이난다”고 언급했다.\n <br/>\n<br/>\n 테슬라처럼 확실한 ‘무기’를 지닌 기업은 변화하는 통상환경에서도 꾸준한 글로벌 수요가 있다는 이 연구원의 설명이다. 그는 앞으로 스페셜티 기업과 커머디티(commodity·일반 상품) 기업의 주가 양극화가 심화될 것으로 내다봤다.\n <br/>\n<br/>\n 국내에선 ‘불닭’을 보유한 삼양식품이나 의료 시

In [41]:
# 다른 여러 파일들을 가져오려고 했으나 전처리가 되어있지 않아 사용 불가 따로 적용해서 찾아보겠음.
# 데이터를 Document로 변환
docs = [Document(page_content = news_info['news_content'],metadata = {'title': news_info['news_title'],'time': news_info['news_first_upload_time']})
    for news_info in news_data]
# 위와 같은 이유로 전처리하는 것을 찾아보겠음.
# 찾아보니까 임베딩 모델이 openaiembeddings를 사용하고 있어서 토큰화가 필요없다. 자동으로 하긴하는데, 전처리를 해주는 것은 좋아보인다.
# 전처리를 하고 임베딩 모델에 넣어서 faiss에 저장해보자.
# 전처리 과정 >> 함수로 정의해 두었습니다다
for i in range(len(docs)):
    docs[i].page_content = preprocess_text(docs[i].page_content)
# 청크로 나누기
splitter = CharacterTextSplitter(chunk_size = 500, chunk_overlap = 50)
split_texts = splitter.split_documents(docs)
embeddings = OpenAIEmbeddings(openai_api_key=api_key)
# faiss에 저장
vector_store = FAISS.from_documents(split_texts, embeddings)

In [44]:
vector_store.save_local(r'C:\Users\RMARKET\Desktop\finance-advisor-bot')

In [47]:
vs = FAISS.load_local(r'C:\Users\RMARKET\Desktop\finance-advisor-bot', embeddings, allow_dangerous_deserialization=True)

In [ ]:
vs.add_documents

In [58]:
load_dotenv()

True

In [60]:
cluster = MongoClient(os.environ.get("mongo")) # 클러스터
db = cluster['Document'] # 뉴스 정보
collection = db["newsdata"] # 내가 지정한 컬렉션 이름

In [61]:
collection.insert_many(news_data)

InsertManyResult([ObjectId('67a450ce5f2b80fa180b0536'), ObjectId('67a450ce5f2b80fa180b0537'), ObjectId('67a450ce5f2b80fa180b0538'), ObjectId('67a450ce5f2b80fa180b0539'), ObjectId('67a450ce5f2b80fa180b053a'), ObjectId('67a450ce5f2b80fa180b053b'), ObjectId('67a450ce5f2b80fa180b053c'), ObjectId('67a450ce5f2b80fa180b053d'), ObjectId('67a450ce5f2b80fa180b053e'), ObjectId('67a450ce5f2b80fa180b053f'), ObjectId('67a450ce5f2b80fa180b0540'), ObjectId('67a450ce5f2b80fa180b0541'), ObjectId('67a450ce5f2b80fa180b0542'), ObjectId('67a450ce5f2b80fa180b0543'), ObjectId('67a450ce5f2b80fa180b0544'), ObjectId('67a450ce5f2b80fa180b0545'), ObjectId('67a450ce5f2b80fa180b0546'), ObjectId('67a450ce5f2b80fa180b0547'), ObjectId('67a450ce5f2b80fa180b0548'), ObjectId('67a450ce5f2b80fa180b0549'), ObjectId('67a450ce5f2b80fa180b054a'), ObjectId('67a450ce5f2b80fa180b054b'), ObjectId('67a450ce5f2b80fa180b054c'), ObjectId('67a450ce5f2b80fa180b054d'), ObjectId('67a450ce5f2b80fa180b054e'), ObjectId('67a450ce5f2b80fa180b05

In [ ]:
# results = collection.find({ "news_website": "maekyung" })
results = collection.find()
t = results.to_list()

[{'_id': ObjectId('67a450ce5f2b80fa180b0536'),
  'news_title': '무역전쟁엔 스페셜티 기업이 성공··· “2월은 저가매수 기회”',
  'news_first_upload_time': '2025-02-04 18:11',
  'news_last_upload_time': None,
  'news_author': '정재원 기자',
  'news_content': '<div style="display:box;border-left:solid 4px rgb(228, 228, 228);padding-left: 20px; padding-right: 20px;">\n  4일 메리츠증권 보고서\n  <br/>\n  테슬라 자율주행 기술처럼\n  <br/>\n  전문성 갖춘 국내 기업 찾아라\n </div>\n <br/>\n<br/>\n 글로벌 통상환경의 ‘불확실성’ 파도로부터 살아남을 수 있는 국내 주식은 ‘스페셜티’(Specialty·전문성)를 갖춘 기업이라는 분석이 나왔다.\n <br/>\n<br/>\n 4일 이수정 메리츠증권 연구원은 2월 투자전망 보고서에서 “국내 주식은 위험 회피 현상이 지나면 장기적으로 무역전쟁의 반사수혜가 기대된다”며 이번 달을 스페셜티 기업들의 저가매수 기회로 삼으라고 조언했다.\n <br/>\n<br/>\n 이수정 연구원은 스페셜티 기업의 대표적 예시로 테슬라를 꼽았다. 테슬라는 독보적인 자율주행 기술을 무기로 시장을 이끌어 온 업계 선두주자다.\n <br/>\n<br/>\n 이 연구원은 “테슬라 자율주행의 사고 전 평균 주행거리는 594만마일(956만km)로, 미국 수동운전자들의 운전 평균값인 70만마일(112만km)와 크게 차이난다”고 언급했다.\n <br/>\n<br/>\n 테슬라처럼 확실한 ‘무기’를 지닌 기업은 변화하는 통상환경에서도 꾸준한 글로벌 수요가 있다는 이 연구원의 설명이다. 그는 앞으로 스페셜티 기업과 커머디티(commodity·일반 상품) 기업의 주가 양극화가 심화될 것으로 내다

In [70]:
for res in results:
    print(res)

{'_id': ObjectId('67a450ce5f2b80fa180b0536'), 'news_title': '무역전쟁엔 스페셜티 기업이 성공··· “2월은 저가매수 기회”', 'news_first_upload_time': '2025-02-04 18:11', 'news_last_upload_time': None, 'news_author': '정재원 기자', 'news_content': '<div style="display:box;border-left:solid 4px rgb(228, 228, 228);padding-left: 20px; padding-right: 20px;">\n  4일 메리츠증권 보고서\n  <br/>\n  테슬라 자율주행 기술처럼\n  <br/>\n  전문성 갖춘 국내 기업 찾아라\n </div>\n <br/>\n<br/>\n 글로벌 통상환경의 ‘불확실성’ 파도로부터 살아남을 수 있는 국내 주식은 ‘스페셜티’(Specialty·전문성)를 갖춘 기업이라는 분석이 나왔다.\n <br/>\n<br/>\n 4일 이수정 메리츠증권 연구원은 2월 투자전망 보고서에서 “국내 주식은 위험 회피 현상이 지나면 장기적으로 무역전쟁의 반사수혜가 기대된다”며 이번 달을 스페셜티 기업들의 저가매수 기회로 삼으라고 조언했다.\n <br/>\n<br/>\n 이수정 연구원은 스페셜티 기업의 대표적 예시로 테슬라를 꼽았다. 테슬라는 독보적인 자율주행 기술을 무기로 시장을 이끌어 온 업계 선두주자다.\n <br/>\n<br/>\n 이 연구원은 “테슬라 자율주행의 사고 전 평균 주행거리는 594만마일(956만km)로, 미국 수동운전자들의 운전 평균값인 70만마일(112만km)와 크게 차이난다”고 언급했다.\n <br/>\n<br/>\n 테슬라처럼 확실한 ‘무기’를 지닌 기업은 변화하는 통상환경에서도 꾸준한 글로벌 수요가 있다는 이 연구원의 설명이다. 그는 앞으로 스페셜티 기업과 커머디티(commodity·일반 상품) 기업의 주가 양극화가 심화될 것으로 내다봤다.\n <br/>